In [2]:
%matplotlib inline
import glob
import matplotlib.pyplot as plt
import pandas as pd
import pulp
import csv


pd.set_option('display.width', 1000)

In [26]:
# create dataframe of past salaries and past performance
fantasy_df = pd.read_csv("../Data/Agg_test_set.csv")

# create dataframe of past salaries and past performance
FaantasyDay = pd.read_csv("../Data/testdata3.csv")

# Print the first five rows of data to the screen
fantasy_df.head()

Name   GID Team  Opp  Home  NewGameFDP  LastFDP     AvgFDP     AvgPTS  LastPT  ...  LastTOV  Last3GameAvgFDP  Last3GameAvgMIN  Last3GameAvgPTS  position      Rank  TeamStdFDP  TeamAvgFDP  TeamMaxFDP  source
0            Brandon Clarke  5837  mem  nor     1        11.8     27.9  24.477778  12.333333      15  ...        0        27.833333        22.672222        12.666667        PF   average   11.347920   23.324267   47.004762    test
1  Nickeil Alexander-Walker  5887  nor  mem     0        14.9     14.9  11.988235   6.088235      10  ...        2        14.666667        14.711111         9.000000        SG  belowAvg   13.590201   23.905789   49.595833    test
2           Dejounte Murray  4963  sas  pho     0        29.4     41.9  27.386111  10.222222      13  ...        2        27.733333        26.638889         9.000000        PG   average   12.239532   22.720471   46.891304    test
3           Anfernee Simons  5662  por  gsw     1        26.9     17.1  15.209091   9.272727      12  ...        0        18.466667        27.966667         7.000000        PG  belowAvg   15.776761   25.353028   54.916000    test
4              Vince Carter  2448  atl  tor     1        11.9      9.2  10.302778   4.916667       5  ...        0        11.500000        13.838889         6.333333        SF  belowAvg   14.513723   21.629093   53.444000    test

[5 rows x 34 columns]

In [27]:
fantasy_df['Name'] = fantasy_df['Name'].replace(' ', '_', regex=True)
fantasy_df

Name   GID Team  Opp  Home  NewGameFDP  LastFDP     AvgFDP     AvgPTS  LastPT  ...  LastTOV  Last3GameAvgFDP  Last3GameAvgMIN  Last3GameAvgPTS  position      Rank  TeamStdFDP  TeamAvgFDP  TeamMaxFDP  source
0               Brandon_Clarke  5837  mem  nor     1        11.8     27.9  24.477778  12.333333      15  ...        0        27.833333        22.672222        12.666667        PF   average   11.347920   23.324267   47.004762    test
1     Nickeil_Alexander-Walker  5887  nor  mem     0        14.9     14.9  11.988235   6.088235      10  ...        2        14.666667        14.711111         9.000000        SG  belowAvg   13.590201   23.905789   49.595833    test
2              Dejounte_Murray  4963  sas  pho     0        29.4     41.9  27.386111  10.222222      13  ...        2        27.733333        26.638889         9.000000        PG   average   12.239532   22.720471   46.891304    test
3              Anfernee_Simons  5662  por  gsw     1        26.9     17.1  15.209091   9.272727      12  ...        0        18.466667        27.966667         7.000000        PG  belowAvg   15.776761   25.353028   54.916000    test
4                 Vince_Carter  2448  atl  tor     1        11.9      9.2  10.302778   4.916667       5  ...        0        11.500000        13.838889         6.333333        SF  belowAvg   14.513723   21.629093   53.444000    test
...                        ...   ...  ...  ...   ...         ...      ...        ...        ...     ...  ...      ...              ...              ...              ...       ...       ...         ...         ...         ...     ...
1753          Donte_DiVincenzo  5740  mil  pho     1        22.9     28.2  22.162500   8.975000      11  ...        2        26.633333        23.311111        13.000000        SG   average   16.267243   22.505904   62.121429    test
1754              Monte_Morris  5191  den  det     0        40.9     18.1  16.368293   7.536585      11  ...        1        16.933333        22.655556         9.000000        PG  belowAvg   13.421538   25.074225   52.200000    test
1755              Eric_Bledsoe  4266  mil  pho     1        28.4     19.5  30.275000  15.055556       8  ...        2        19.533333        23.072222         9.333333        PG  advanced   16.267243   22.505904   62.121429    test
1756               Gary_Harris  4678  den  det     0         6.1     29.6  21.721622  11.000000      15  ...        1        24.000000        31.055556        10.666667        SG   average   13.421538   25.074225   52.200000    test
1757           Sekou_Doumbouya  5866  det  den     1        21.0      8.8  14.000000   7.812500       4  ...        0        23.933333        29.944444        14.666667        PF  belowAvg   13.478020   22.557781   52.116000    test

[1758 rows x 34 columns]

In [28]:
fantasy_df.corr()['NewGameFDP']

GID               -0.157108
Home              -0.016433
NewGameFDP         1.000000
LastFDP            0.499434
AvgFDP             0.695561
AvgPTS             0.650320
LastPT             0.453602
AvgMIN             0.571736
LastMIN            0.440583
AvgFGM             0.470042
LastFGM            0.129512
AvgFGA             0.448168
LastFGA            0.158123
Avg3PTS            0.278540
Last3PTS           0.152855
AvgREB             0.446578
LastREB            0.316366
AvgAST             0.492237
LastAST            0.401287
AvgSTL             0.355538
AvgTOV             0.605825
LastTOV            0.373364
Last3GameAvgFDP    0.631205
Last3GameAvgMIN    0.521578
Last3GameAvgPTS    0.582370
TeamStdFDP         0.072262
TeamAvgFDP         0.141099
TeamMaxFDP         0.065289
Name: NewGameFDP, dtype: float64

In [29]:
to_drop = ['GID', 'Home', 'LastFGM', 'LastFGA', 'Avg3PTS', 'LastTOV', 'AvgSTL', 'TeamStdFDP',  'TeamAvgFDP', 'TeamMaxFDP', \
           'Rank', 'source', 'Team', 'Opp']
fantasy_df.drop(to_drop, axis=1, inplace = True)
fantasy_df

Name  NewGameFDP  LastFDP     AvgFDP     AvgPTS  LastPT     AvgMIN    LastMIN    AvgFGM    AvgFGA  Last3PTS    AvgREB  LastREB    AvgAST  LastAST    AvgTOV  Last3GameAvgFDP  Last3GameAvgMIN  Last3GameAvgPTS position
0               Brandon_Clarke        11.8     27.9  24.477778  12.333333      15  21.378704  25.316667  4.500000  7.222222         1  5.722222        2  1.500000        3  0.972222        27.833333        22.672222        12.666667       PF
1     Nickeil_Alexander-Walker        14.9     14.9  11.988235   6.088235      10  13.735784  13.966667  1.911765  5.764706         2  2.147059        2  1.941176        1  1.000000        14.666667        14.711111         9.000000       SG
2              Dejounte_Murray        29.4     41.9  27.386111  10.222222      13  24.170833  32.850000  4.222222  8.638889         0  6.027778       12  4.138889        5  2.111111        27.733333        26.638889         9.000000       PG
3              Anfernee_Simons        26.9     17.1  15.209091   9.272727      12  22.714394  35.250000  3.522727  8.590909         1  2.636364        3  1.454545        1  0.977273        18.466667        27.966667         7.000000       PG
4                 Vince_Carter        11.9      9.2  10.302778   4.916667       5  15.293519  10.133333  1.750000  5.250000         1  1.861111        1  0.916667        0  0.555556        11.500000        13.838889         6.333333       SF
...                        ...         ...      ...        ...        ...     ...        ...        ...       ...       ...       ...       ...      ...       ...      ...       ...              ...              ...              ...      ...
1753          Donte_DiVincenzo        22.9     28.2  22.162500   8.975000      11  22.738750  25.600000  3.400000  7.550000         1  4.500000        6  2.275000        2  1.175000        26.633333        23.311111        13.000000       SG
1754              Monte_Morris        40.9     18.1  16.368293   7.536585      11  18.219919  25.850000  3.024390  6.780488         1  1.536585        3  3.341463        3  0.585366        16.933333        22.655556         9.000000       PG
1755              Eric_Bledsoe        28.4     19.5  30.275000  15.055556       8  26.001852  27.700000  4.027778  9.194444         0  4.638889        5  5.138889        5  2.222222        19.533333        23.072222         9.333333       PG
1756               Gary_Harris         6.1     29.6  21.721622  11.000000      15  32.896847  24.366667  4.135135  9.810811         2  2.729730        3  2.189189        2  1.027027        24.000000        31.055556        10.666667       SG
1757           Sekou_Doumbouya        21.0      8.8  14.000000   7.812500       4  18.439583  27.583333  2.375000  5.312500         1  3.125000        4  0.375000        0  0.562500        23.933333        29.944444        14.666667       PF

[1758 rows x 20 columns]

In [32]:
temp['Name'] = temp['Name'].replace(' ', '_', regex=True)
temp

Name   GID        Date Team  Opp  Home  GTime(ET)  Team_pts  Opp_pts  Win  ...  STL  BLK  TOV  3P  FGM  FGA    FG% FTM  FTA     FT%
0                Louis_Williams  3816  2019-10-22  lac  lal     1       22.5       112      102    1  ...    1    0    2   1    8   14  57.1%   4    4  100.0%
1                    Quinn_Cook  4863  2019-10-22  lal  lac     0       22.5       102      112    0  ...    0    0    1   0    2    7    NaN   0    0     NaN
2      Nickeil_Alexander-Walker  5887  2019-10-22  nor  tor     0       20.0       122      130    0  ...    2    0    1   1    1   10    NaN   0    0     NaN
3                  Jrue_Holiday  4212  2019-10-22  nor  tor     0       20.0       122      130    0  ...    0    2    5   1    6   15  40.0%   0    2     NaN
4                  LeBron_James  3541  2019-10-22  lal  lac     0       22.5       102      112    0  ...    1    1    5   1    7   19  36.8%   3    4  100.0%
...                         ...   ...         ...  ...  ...   ...        ...       ...      ...  ...  ...  ...  ...  ...  ..  ...  ...    ...  ..  ...     ...
15687               Paul_Watson  5958  2020-02-02  tor  chi     1       15.0       129      102    1  ...    0    0    0   0    0    0   0.0%   1    2  100.0%
15688              Monte_Morris  5191  2020-02-02  den  det     0       12.5       123      128    0  ...    1    0    0   2    8   15  53.3%   1    1  100.0%
15689              Eric_Bledsoe  4266  2020-02-02  mil  pho     1       14.0       129      108    1  ...    0    1    1   2    5    8  62.5%   0    1     NaN
15690               Gary_Harris  4678  2020-02-02  den  det     0       12.5       123      128    0  ...    0    0    2   0    1    6  16.7%   1    2     NaN
15691           Sekou_Doumbouya  5866  2020-02-02  det  den     1       12.5       128      123    1  ...    0    0    2   2    6   12  50.0%   3    4  100.0%

[15692 rows x 33 columns]

In [33]:
columns = ['Name','FD_Sal']
temp = temp[columns]

In [34]:
fantasy_df = pd.merge(fantasy_df, temp, how='left',on='Name')
fantasy_df.columns

Index(['Name', 'NewGameFDP', 'LastFDP', 'AvgFDP', 'AvgPTS', 'LastPT', 'AvgMIN', 'LastMIN', 'AvgFGM', 'AvgFGA', 'Last3PTS', 'AvgREB', 'LastREB', 'AvgAST', 'LastAST', 'AvgTOV', 'Last3GameAvgFDP', 'Last3GameAvgMIN', 'Last3GameAvgPTS', 'position', 'FD_Sal'], dtype='object')

# LINEAR MODELING

In [35]:
# formulate linear programming problem
problem = pulp.LpProblem("Optimal Lineup", pulp.LpMaximize)

#Defining Variables

In [36]:
# initialize variables
playerPositions = fantasy_df['position'].tolist()
playerNames = fantasy_df['Name'].tolist()
playerCosts = tuple(fantasy_df['FD_Sal'])
playerPoints = tuple(fantasy_df['NewGameFDP'])
salaryCap = 60000
numOfPlayers = range(len(playerNames))

In [37]:
# create variable to represent each player
playerInLineup = pulp.LpVariable.dicts("Player", [i for i in numOfPlayers], 0, 1, cat="Binary")


#Creating the Objective(s)

In [38]:
# Objective: maximize sum of player points in FanDuel
problem += pulp.lpSum(playerInLineup[i] * playerPoints[i] for i in numOfPlayers)
print(problem)

Optimal_Lineup:
MAXIMIZE
11.8*Player_0 + 11.8*Player_1 + 11.8*Player_10 + 29.4*Player_100 + 18.6*Player_1000 + 2.7*Player_10000 + 2.7*Player_10001 + 2.7*Player_10002 + 2.7*Player_10003 + 2.7*Player_10004 + 2.7*Player_10005 + 2.7*Player_10006 + 2.7*Player_10007 + 2.7*Player_10008 + 2.7*Player_10009 + 18.6*Player_1001 + 2.7*Player_10010 + 2.7*Player_10011 + 2.7*Player_10012 + 2.7*Player_10013 + 6.4*Player_10014 + 6.4*Player_10015 + 6.4*Player_10016 + 6.4*Player_10017 + 6.4*Player_10018 + 6.4*Player_10019 + 34.7*Player_1002 + 6.4*Player_10020 + 6.4*Player_10021 + 6.4*Player_10022 + 6.4*Player_10023 + 6.4*Player_10024 + 6.4*Player_10025 + 6.4*Player_10026 + 6.4*Player_10027 + 6.4*Player_10028 + 6.4*Player_10029 + 34.7*Player_1003 + 6.4*Player_10030 + 6.4*Player_10031 + 6.4*Player_10032 + 6.4*Player_10033 + 6.4*Player_10034 + 6.4*Player_10035 + 6.4*Player_10036 + 6.4*Player_10037 + 6.4*Player_10038 + 6.4*Player_10039 + 34.7*Player_1004 + 6.4*Player_10040 + 6.4*Player_10041 + 6.4*Player_1004

# Defining the Contraints

In [39]:
# constraint n1: each player can only be chosen at most once
for i in numOfPlayers:
    problem += pulp.lpSum(playerInLineup[i]) <= 1
    

In [40]:
# constraint n2: sum of player costs cannot be more than or equal to FanDuel Salary cap ($ 60,000)
problem += sum(playerInLineup[i] * playerCosts[i] for i in numOfPlayers) <= salaryCap

In [41]:
# constraint n3: teams can have up to 9 players
problem += pulp.lpSum(problem.variables()) == 9

#Player Positions

In [43]:
# constraint n4: number of PG = 2
pointguards = tuple(fantasy_df['position'] == 'PG')
problem += pulp.lpSum(playerInLineup[i] * pointguards[i] for i in numOfPlayers) >=1
problem += pulp.lpSum(playerInLineup[i] * pointguards[i] for i in numOfPlayers) <= 2

In [44]:
# constraint n5: number of SG = 2
shootinguard = tuple(fantasy_df['position'] == 'SG')
problem += pulp.lpSum(playerInLineup[i] * shootinguard[i] for i in numOfPlayers) >=2
problem += pulp.lpSum(playerInLineup[i] * shootinguard[i] for i in numOfPlayers) <= 2

In [45]:
# constraint n6: number of SF = 2
smallforward = tuple(fantasy_df['position'] == 'SF')
problem += pulp.lpSum(playerInLineup[i] * smallforward[i] for i in numOfPlayers) >=2
problem += pulp.lpSum(playerInLineup[i] * smallforward[i] for i in numOfPlayers) <= 2

In [46]:
# constraint n7: number of PF = 2
powerforward = tuple(fantasy_df['position'] == 'PF')
problem += pulp.lpSum(playerInLineup[i] * powerforward[i] for i in numOfPlayers) >=2
problem += pulp.lpSum(playerInLineup[i] * powerforward[i] for i in numOfPlayers) <= 2

In [47]:
# constraint n8: number of C = 1
center = tuple(fantasy_df['position'] == 'C')
problem += pulp.lpSum(playerInLineup[i] * center[i] for i in numOfPlayers) >=1
problem += pulp.lpSum(playerInLineup[i] * center[i] for i in numOfPlayers) <= 1

# Solving the Problem

In [48]:
# calculating predicted lineup
cost = 0
points = 0

predicted = set()
if problem.solve() == 1:
    for pos in range(len(numOfPlayers)):
        if playerInLineup[pos].value() == 1:
            name = playerNames[pos]
            predicted.add(name)
            cost += playerCosts[pos]
            points += playerPoints[pos]
            print (playerNames[pos], playerPositions[pos], playerCosts[pos],playerPoints[pos])
    print ('-------------------')
    print (f"The total cost is =: {cost}")
    print (f"The predicted FanDuel points: {points}")
else:
    print ('Error finding solution')

Damian_Lillard PG 8500 84.5
Damian_Lillard PG 8500 84.5
John_Collins PF 7300 67.2
John_Collins PF 7400 67.2
Eric_Gordon SF 3700 68.7
Eric_Gordon SF 3800 68.7
Khris_Middleton SG 6100 70.0
Khris_Middleton SG 6100 70.0
Nikola_Jokic C 8500 80.5
-------------------
The total cost is =: 59900
The predicted FanDuel points: 661.3
